![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 2. <i>Zaawansowane użycie pamięci tłumaczeń</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Wiemy już, do czego służy pamięć tłumaczeń. Spróbujmy przeprowadzić mały research, którego celem będzie odkrycie, w jaki sposób do pamięci tłumaczeń podchodzą najwięksi producenci oprogramowania typu CAT.


### Ćwiczenie 1: Wykonaj analizę funkcjonalności pamięci tłumaczeń w programach SDL Trados Studio 2021 oraz Kilgray memoQ. Dla obu programów wypisz funkcje, które są związane z TM oraz zaznacz, które funkcje są wspólne dla obu programów oraz których funkcji Tradosa brakuje w memoQ oraz odwrotnie.

Odpowiedź:

Jedną z funkcji dostępnych we wszystkich większych programach do wspomagania tłumaczenia jest znajdowanie bardzo pewnych dopasowań w pamięci tłumaczeń. Są one zwane **ICE** (In-Context Exact match) lub 101% match. Są to takie dopasowania z pamięci tłumaczeń, dla których nie tylko zdanie źródłowe z TM jest identyczne z tłumaczonym, ale także poprzednie zdanie źródłowe z TM zgadza się z poprzednim zdaniem tłumaczonym oraz następne z TM z następnym tłumaczonym.

 Rozważmy przykładową pamięć tłumaczeń z poprzednich zajęć (można do niej dorzucić kilka przykładów):

In [22]:
translation_memory = [
                      ('Wciśnij przycisk Enter', 'Press the ENTER button'), 
                      ('Sprawdź ustawienia sieciowe', 'Check the network settings'),
                      ('Drukarka jest wyłączona', 'The printer is switched off'),
                      ('Wymagane ponowne uruchomienie komputera', 'System restart required')
                     ]

### Ćwiczenie 2: Zaimplementuj funkcję ice_lookup, przyjmującą trzy parametry: aktualnie tłumaczone zdanie, poprzednio tłumaczone zdanie, następne zdanie do tłumaczenia. Funkcja powinna zwracać dopasowania typu ICE. Nie pozwól, aby doszło do błędów podczas sprawdzania pierwszego i ostatniego przykładu w pamięci (ze względu na brak odpowiednio poprzedzającego oraz następującego przykładu).

In [43]:

def ice_lookup(sentence, prev_sentence, next_sentence):
        for index in range(len(translation_memory)):
                if index == 0:
                        continue
                elif index + 1 >= len(translation_memory):
                        return []
                else:
                        middleText = translation_memory[index]
                        prevText = translation_memory[index-1]
                        nextText = translation_memory[index+1]
                        if(sentence == middleText[0] and prev_sentence == prevText[0] and next_sentence == nextText[0]):
                                return [middleText[1], prevText[1], nextText[1]]
                        
        return []
     

        
        
ice_lookup('Drukarka jest wyłączona','Sprawdź ustawienia sieciowe','Wymagane ponowne uruchomienie komputera')                        


['The printer is switched off',
 'Check the network settings',
 'System restart required']

Inną powszechnie stosowaną techniką przeszukiwania pamięci tłumaczeń jest tzw. **fuzzy matching**. Technika ta polega na wyszukiwaniu zdań z pamięci, które są tylko podobne do zdania tłumaczonego. Na poprzednich zajęciach wykonywaliśmy funkcję tm_lookup, która pozwalała na różnicę jednego słowa.

Zazwyczaj jednak funkcje fuzzy match posiadają znacznie szersze możliwości. Ich działanie opiera się na zdefiniowaniu funkcji $d$ dystansu pomiędzy zdaniami $x$ i $y$. Matematycznie, funkcja dystansu posiada następujące właściwości:
1. $\forall_{x,y} d(x,y)\geqslant 0$
2. $\forall_{x,y} d(x,y)=0 \Leftrightarrow x=y$
3. $\forall_{x,y} d(x,y)=d(y,x)$
4. $\forall_{x,y,z} d(x,y) + d(y,z)\geqslant d(x,z)$

Rozważmy następującą funkcję:

In [44]:
def sentence_distance(x,y):
    return abs(len(y) - len(x))

### Ćwiczenie 3: Czy to jest poprawna funkcja dystansu? Które warunki spełnia?

Odpowiedź: Tak, Spełnia warunki dla 1,2,3,4, 

A teraz spójrzmy na taką funkcję:

In [4]:
def sentence_distance(x,y):
    if (x == y):
        return 0
    else:
        return 3

### Ćwiczenie 4: Czy to jest poprawna funkcja dystansu? Które warunki spełnia?

Odpowiedź: Nie, Spełnia dla warunku 3, poniewaz x = 4, y = 4, to wychodzi d(x,y) = 3, a nie 0

Wprowadźmy jednak inną funkcję dystansu - dystans Levenshteina. Dystans Levenshteina pomiędzy dwoma łańcuchami znaków definiuje się jako minimalną liczbę operacji edycyjnych, które są potrzebne do przekształcenia jednego łańcucha znaków w drugi. Wyróżniamy trzy operacje edycyjne:
* dodanie znaku
* usunięcie znaku
* zamiana znaku na inny

### Ćwiczenie 5: Czy dystans Levenshteina jest poprawną funkcją dystansu? Uzasadnij krótko swoją odpowiedź sprawdzając każdy z warunków.

Odpowiedź:

W Pythonie dostępna jest biblioteka zawierająca implementację dystansu Levenshteina. Zainstaluj ją w swoim systemie przy użyciu polecenia:

`pip3 install python-Levenshtein`

I wypróbuj:

In [45]:
from Levenshtein import distance as levenshtein_distance

levenshtein_distance("kotek", "kotki")


2

Funkcja ta daje nam możliwość zdefiniowania podobieństwa pomiędzy zdaniami:

In [46]:
def levenshtein_similarity(x,y):
    return 1 - levenshtein_distance(x,y) / max(len(x), len(y))

Przetestujmy ją!

In [47]:
levenshtein_similarity('Program jest uruchomiony', 'Program jest uruchamiany')

0.9166666666666666

In [48]:
levenshtein_similarity('Spróbuj wyłączyć i włączyć komputer', 'Spróbuj włączyć i wyłączyć komputer')

0.9428571428571428

In [49]:
levenshtein_similarity('Spróbuj wyłączyć i włączyć komputer', 'Nie próbuj wyłączać i włączać drukarki')

0.631578947368421

### Ćwiczenie 6: Napisz funkcję fuzzy_lookup, która wyszuka w pamięci tłumaczeń wszystkie zdania, których podobieństwo Levenshteina do zdania wyszukiwanego jest większe lub równe od ustalonego progu.

In [51]:
def fuzzy_lookup(sentence, threshold):
    return [entry[1] for entry in translation_memory if levenshtein_similarity(entry[0],sentence ) > threshold]

fuzzy_lookup('Wciśnij przycisk Enter', 0.5)

['Press the ENTER button']